## Project Goals
- Scrape Amazon product prices, ratings, and reviews
- Build a Tableau dashboard for visualization and analysis

## Scraping Amazon Products

### Install libraries


In [4]:
!pip3 install fake-useragent==1.5.1
!pip3 install --upgrade pip setuptools wheel
!pip3 install requests beautifulsoup4 pandas numpy stats


Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable
  Preparing metadata (setup.py) ... done
  Created wheel for stats: filename=stats-0.1.2a0-py3-none-any.whl size=24331 sha256=638884cf14d150bc4de3a85f71fe21f282bae518c87737a7798b990d15959cd1
  Stored in directory: /Users/michiko/Library/Caches/pip/wheels/15/a4/f5/a7431ca9ac466505e866f76a55ae9f94192eafb0f634fce49f
Successfully built stats


### Scrape Amazon Product Data

In [12]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import concurrent.futures
import random
import time
import threading
from fake_useragent import UserAgent

# Custom headers to mimic a real browser
user_agent = UserAgent()
headers = {"User-Agent": user_agent.random}  # random user agent
custom_headers = {
    'User-Agent': "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/120.0.0.0 Safari/537.36",
    'Accept-Language': 'da, en-gb, en',
    'Accept-Encoding': 'gzip, deflate, br',
    'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,image/avif,image/webp,*/*;q=0.8',
    'Referer': 'https://www.google.com/'
}

# Search queries and number of pages to scrape
num_pages = 7
search_queries =["skincare", "serum", "sun+screen", "moisturizer", "cleanser", "retinol+cream", "sheet+mask", "face+oil", "cleansing+oil", "night+cream", "korean+skincare"] #"gel+moisturizer"
product_list = []
lock = threading.Lock()  # To ensure thread-safe data collection

# Function to fetch HTML content with retries
def fetch(url):
    print(f"🟡 Fetching URL: {url}")

    for _ in range(3):  # Retry up to 3 times
        try:
            time.sleep(random.uniform(5,10))  # Add delay to avoid detection
            response = requests.get(url, headers=custom_headers, timeout=10)

            print(f"🟢 Response Status Code: {response.status_code}")
            
            if response.status_code == 200:
                print("✅ Successfully fetched HTML")
                return response.text  # Returns HTML

            elif response.status_code == 503:
                print(f"❌ CAPTCHA Detected for {url} (503)")
                return None 
            
            else:
                print(f"❌ Other Error: {response.status_code} on {url}")
                return None  # Other errors

        except requests.RequestException as e:
            print(f"❌ Request failed: {e}")
            time.sleep(random.uniform(2, 4))  # Retry delay

    return None

# Function to scrape product listings from search page
def scrape_search_page(search_query, page):
    url = f"https://www.amazon.com/s?k={search_query}&page={page}"
    html = fetch(url) #calls fetch function

    if html:
        soup = BeautifulSoup(html, "html.parser")
        products = soup.find_all("div", {"data-component-type": "s-search-result"})

        if not products:
            print(f"❌ No products found on page {page} for {search_query}. Check the HTML structure.")
            return
        
        for product in products:
            category = search_query
            title_tag = product.find("h2", class_="a-size-base-plus")
            link_tag = product.find("a", class_="a-link-normal s-no-outline")
            price_tag = product.find("span", {"class": "a-price"})
            original_price_div = product.find("div", class_="a-section aok-inline-block")
            original_price_tag = original_price_div.find("span", class_="a-offscreen") if original_price_div else None
            brand_tag = product.find("span", class_="a-size-base-plus a-color-base")  # Brand in search page
            num_ratings_tag = product.find("span", {"class": "a-size-base s-underline-text"})
            rating_tag = product.find("span", class_="a-icon-alt")

            if title_tag and link_tag:
                title = title_tag.text.strip()
                product_url = f"https://www.amazon.com{link_tag['href']}"

                # Extract prices/ratings/brand
                price = price_tag.find("span", class_="a-offscreen").text.strip() if price_tag and price_tag.find("span", class_="a-offscreen") else "N/A"
                original_price = original_price_tag.text.strip() if original_price_tag else "N/A"
                num_ratings = num_ratings_tag.text.strip() if num_ratings_tag else "N/A"
                rating = rating_tag.text.strip() if rating_tag else "N/A"
                brand = brand_tag.text.strip() if brand_tag else "N/A"

                print(f"✅ Extracted: Title={title}, Brand={brand}, Price={price}, URL={product_url}")

                # Append product to list
                with lock:
                    product_list.append([title, brand, price, original_price, rating, num_ratings, product_url, category])
                    print(f"📌 Appended to product_list: {title} | Brand: {brand}")

                # If brand is missing, scrape product page
                if brand == "N/A":
                    print(f"🔍 No brand found. Scraping PDP for {title}...")
                    scrape_product_page(title, product_url, price, original_price, rating, num_ratings,category)

        print(f"✅ Scraped {len(products)} products from search results for query: {search_query}, page {page}")

    else:
        print(f"❌ Failed to fetch HTML for {url}. Check internet connection or CAPTCHA!")

# Function to scrape product details from a product pag
def scrape_product_page(title, product_url, search_price, search_original_price, rating, num_ratings, category):
    html = fetch(product_url)

    if html:
        soup = BeautifulSoup(html, "html.parser")

        # Extract brand from PDP
        brand = "N/A"
        brand_tag = soup.find("a", {"id": "bylineInfo"})
        if brand_tag:
            brand = brand_tag.text.strip()

        print(f"Scraping Product Page: {title}, Brand: {brand}, Price: {search_price}")

        # Append data to the product list
        with lock:
            product_list.append([title, brand, search_price, search_original_price, rating, num_ratings, product_url, category])

# Main function to execute multi-threaded scraping
def main():
    with concurrent.futures.ThreadPoolExecutor(max_workers=7) as executor:
        task_list = []
        for search_query in search_queries:
            for page in range(1, num_pages + 1):
                task_list.append(executor.submit(scrape_search_page, search_query, page))

        # Wait for all tasks to complete
        concurrent.futures.wait(task_list)

# Run scraper
start_time = time.time()
main()
end_time = time.time()

# Save results to an Excel file
df = pd.DataFrame(product_list, columns=["title", "brand", "price", "original price", "rating", "number of ratings", "product url", "category"])
df.to_excel("amazon_multithreaded_new.xlsx", index=False)
print(f"✅ Scraping complete in {end_time - start_time:.2f} seconds & saved to 'amazon_multithreaded_new.xlsx'")


/Users/michiko/Library/Python/3.9/lib/python/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(


🟡 Fetching URL: https://www.amazon.com/s?k=skincare&page=1
🟡 Fetching URL: https://www.amazon.com/s?k=skincare&page=2
🟡 Fetching URL: https://www.amazon.com/s?k=skincare&page=3
🟡 Fetching URL: https://www.amazon.com/s?k=skincare&page=4
🟡 Fetching URL: https://www.amazon.com/s?k=skincare&page=5
🟡 Fetching URL: https://www.amazon.com/s?k=skincare&page=6
🟡 Fetching URL: https://www.amazon.com/s?k=skincare&page=7
🟢 Response Status Code: 200
✅ Successfully fetched HTML
✅ Extracted: Title=NEWKEY LED Face Mask Light Therapy,Red Light Therapy for Face Wrinkle Blue Light Therapy Mask for Face Acne,150LEDs,10 Min Auto Shut off, Wired, Brand=N/A, Price=$150.89, URL=https://www.amazon.com/sspa/click?ie=UTF8&spc=MTo1NTIwOTc2NjQ3ODY4NDY4OjE3Mzk2NTUwNDc6c3BfYXRmX25leHQ6MzAwMjk1MDUxODA1NDAyOjowOjo&url=%2FLight-Therapy-NEWKEY-Facial-System%2Fdp%2FB01MDK70V9%2Fref%3Dsr_1_193_sspa%3Fdib%3DeyJ2IjoiMSJ9.nhQY3HfJ5tKYZh4JTFmTQwKRtfefGIUg116pk1qnWIEgpTFvBbXYQYG2hs49MdoKWOSCnMSmzvcBAOrr56CeDZbv-vbuIbHGzbVjK6nO

### Clean and prepare data
- Check and fix for missing values
- Remove duplicates


In [20]:
import pandas as pd
import re
import numpy as np
from scipy import stats

#Function to extract brand
def extract_brand(text):
    if pd.notna(text): 
        if "Visit the" in text:
            match = re.search(r"Visit the (.+?) Store", text)
        elif "Brand:":
            match = re.search(r"Brand: \s*(.+)",text)
        else:
            return text
        
        if match:
            return match.group(1)
        
    return text


df = pd.read_excel("amazon_multithreaded_new.xlsx")

#Remove rows with missing titles/prices
df.dropna(subset=["title", "brand" ,"price", "number of ratings"], inplace=True)

# Remove duplicates
df.drop_duplicates(subset=["title"], keep="first", inplace=True)

# Convert N/A to pandas NA
df.replace("N/A", pd.NA, inplace=True)

# Fill missing values
df.fillna({"brand": "Unknown", "rating": "No rating", "number of ratings": 0}, inplace=True)

#Extract the brand name
df["brand"] = df["brand"].apply(extract_brand)

#Extract the numeric part only in the rating
df["rating"] = df["rating"].str.extract(r"([\d.]+)").astype(float)

#Remove $ and conver to float
df["price"] = df["price"].astype(str).str.replace(",", "").str.replace("$", "").astype(float)
df["original price"] = df["original price"].astype(str).str.replace(",", "").str.replace("$", "").astype(float)

#Remove commas
df["number of ratings"] = df["number of ratings"].astype(str).str.replace(",", "").astype(int)

#Remove extreme values using zscore
df["z-score"] = np.abs(stats.zscore(df['price']))
df = df[df['z-score'] < 3].drop(columns=['z-score'])

#Fix the data for category
df["category"] = df["category"].str.replace("+", " ")

df.to_excel("clean_amazon_data.xlsx", index=False)

df.sample(20)


title           brand  \
6848  Cetaphil Night Moisturizer for Face, Hydrating...        Cetaphil   
6946  L'Oreal Paris Age Perfect Collagen Expert Anti...   L'Oreal Paris   
1223  MAELOVE Vitamin C Serum, Glow Maker with Vitam...         MAELOVE   
7276  L'Oreal Paris Revitalift 0.3% Pure Retinol Nig...   L'Oreal Paris   
6641  Special Shampoo, Deep Cleans, Refreshes Scalp,...        Tea Tree   
3641  Aveeno Calm + Restore Redness Relief Foaming C...          Aveeno   
2575  CeraVe Oil Control Moisturizing Gel-Cream, Fac...          CeraVe   
6201  Facial Cleanser - Snow Aqua 0 LHA Toning Clean...           NOONI   
1525  Neutrogena Beach Defense Body Spray Sunscreen ...      Neutrogena   
6567  wonder Black Rice Triple AHA Gentle Cleansing ...        HARUHARU   
1805  Sun Bum Original SPF 30 Sunscreen Lotion | Veg...         Sun Bum   
7447  Pacifica Retinol Serum for Face - Wake Up Beau...        Pacifica   
6386  Skin Food Face Care Nourishing Oil-to-Milk Cle...          Weleda   
3987  Good Molecules 1% Retinol Night Oil 12ml/0.40o...  Good Molecules   
3609  Ursa Major Fantastic Face Wash | Natural, Vega...      Ursa Major   
2898  L'Oréal Paris Revitalift Anti-Wrinkle and Firm...   L'Oreal Paris   
4838  IREV Pack of 10 Pink Rose O2 Bubble Face Masks...            IREV   
5210  FARMSKIN Organic Face Mask, 12 pcs - Hydrating...        FARMSKIN   
3665  I'm from Mugwort Gel Cleanser 150ml, Mugwort 6...        I'm from   
333   Thayers Alcohol-Free Rose Petal Witch Hazel Fa...         THAYERS   

      price  original price  rating  number of ratings  \
6848  13.49           14.49     4.5                325   
6946  14.99           15.97     4.5               6257   
1223  39.48             NaN     4.4                359   
7276  30.13           31.99     4.5              12181   
6641  20.00             NaN     4.6              59319   
3641   9.97           14.69     4.4               1218   
2575  16.18           19.99     4.6                609   
6201  20.99             NaN     4.3                158   
1525   9.88           13.19     4.7               9476   
6567  13.10             NaN     4.5                202   
1805  22.98             NaN     4.7               2848   
7447  19.99           24.00     4.5               4890   
6386  19.99             NaN     4.5                340   
3987  12.00             NaN     4.6                579   
3609  32.00             NaN     4.6               1594   
2898  13.85           20.99     4.6               4780   
4838  12.99             NaN     4.5                 33   
5210  18.90             NaN     4.6               1612   
3665  18.00             NaN     4.2                 75   
333   10.53             NaN     4.7             127943   

                                            product url       category  
6848  https://www.amazon.com/Cetaphil-Moisturizer-Li...    night cream  
6946  https://www.amazon.com/LOreal-Paris-Moisturize...    night cream  
1223  https://www.amazon.com/Maelove-Glow-Maker-Vita...          serum  
7276  https://www.amazon.com/LOreal-Paris-Revitalift...    night cream  
6641  https://www.amazon.com/Tea-Tree-Special-Shampo...  cleansing oil  
3641  https://www.amazon.com/Aveeno-Cleanser-Appeara...       cleanser  
2575  https://www.amazon.com/CeraVe-Moisturizing-Moi...    moisturizer  
6201  https://www.amazon.com/NOONI-Korean-Cleansing-...  cleansing oil  
1525  https://www.amazon.com/Neutrogena-Protection-S...     sun screen  
6567  https://www.amazon.com/HARUHARU-Cleansing-Hydr...  cleansing oil  
1805  https://www.amazon.com/Sun-Bum-Octinoxate-Oxyb...     sun screen  
7447  https://www.amazon.com/Pacifica-Retinol-Serum-...    night cream  
6386  https://www.amazon.com/Weleda-Nourishing-Clean...  cleansing oil  
3987  https://www.amazon.com/Good-Molecules-Retinol-...  retinol cream  
3609  https://www.amazon.com/Ursa-Major-Natural-Crue...       cleanser  
2898  https://www.amazon.com/LOreal-Paris-RevitaLift...    moisturizer  
4838  https://